In [2]:
%run ../../Common/UtilityClustering

ModuleNotFoundError: No module named 'pyspark'

In [ ]:
%run ../../Common/UtilityNLP

In [ ]:
df=spark.read.load('abfss://tables@palignedscrivadl01azwe.dfs.core.windows.net/DP_Check_Scrivania_PDB_CURATED').select(col("`boapclpratica.idcase`").alias("idcase"),col("`boapclanomalie.descrizione`").alias("descrizione"),col("`boapclanomalie.statoanomalia`").alias("statoanomalia"),col("`boapclpratica.dataapertura`").alias("dataapertura")).where("descrizione!='NULL' and descrizione!='' and descrizione!='Verifica Documenti'").distinct()
df.cache()
df.display()

In [ ]:
model = nlp_pipeline_bert_sentence_embedding("descrizione").fit(df)
result_bert = model.transform(df)

sentence_detector_dl download started this may take some time.
Approximate size to download 514.9 KB
[OK!]
stopwords_it download started this may take some time.
Approximate size to download 2.4 KB
[OK!]
distilbert_embeddings_BERTino download started this may take some time.
Approximate size to download 241.3 MB
[OK!]


In [ ]:
result_bert.cache()
result_bert.display()

In [ ]:
print("# dataset originale: {}".format(df.count()))
print("# dataset nuovo: {}".format(result_bert.count()))

# dataset originale: 9451
# dataset nuovo: 9451


In [ ]:
result_df_exp=convert_sentence_embedding_in_col(result_bert,["idcase","descrizione","dataapertura"])
result_df_exp.display()

In [ ]:
col_features=result_df_exp.columns[4:]
result_df_exp_filled = result_df_exp.dropna()
result, pca_model, loadings=pipelineStandardPCA(result_df_exp_filled, col_features, 30)

Varianza spiegata da ogni componente principale:  [0.18947432145362986,0.11338513584630974,0.06497188298798953,0.04952377637203366,0.0420362248666462,0.03834494027666791,0.029671068006980876,0.02580525659760042,0.02411706639026064,0.0200160411787744,0.017474317424725407,0.014480427184574578,0.013787997032306064,0.012485976531833724,0.012084377603884982,0.011172431437225723,0.010712330081345589,0.009789980412166246,0.00935051733100518,0.008543594977668193,0.008216760715387359,0.00809922970435507,0.007397771929659483,0.00693154164646445,0.006507562892636402,0.006077098608224935,0.005953699717257385,0.005609083247177442,0.00539736631198553,0.005180152159497599]
Varianza totale: 0.7825979309262747


In [ ]:
cumulativePCwithVariance(pca_model)

In [ ]:
silhouetteClusteringKMeans(result,"pca_features",m=2,n=20,i=2)

In [ ]:
predictions_cluster_final, final_model=defineClustering(result, 12)

Uploading artifacts:   0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
predictions_cluster_final.select("idcase","descrizione","dataapertura","sentence","prediction").distinct().display()

In [ ]:
plotPCA3DInterattivo(predictions_cluster_final.where("dataapertura >= '2024-06-01'"), features='pca_features', predictions='prediction', additional_column='descrizione')

In [ ]:
plotClustering3DInterattivo(predictions_cluster_final.where("dataapertura >= '2024-06-01'"), features='pca_features', predictions='prediction', additional_column='descrizione')

In [ ]:
docs_per_topic = predictions_cluster_final.groupby('prediction').agg(concat_ws(' ', collect_list(col("sentence"))).alias('Doc'))

topN=top_n_words(docs_per_topic, inputCol="Doc", outputCol="features", ngram=3, N=10, targetCol="prediction")

topN.display()

Uploading artifacts:   0%|          | 0/4 [00:00<?, ?it/s]

prediction topN_words 0 List(didentita codic fiscal, identita codic fiscal, fronteretro carta didentit, documento identit codic, identit codic fiscal, fotocopi fronteretro carta, carta didentita codic, codic fiscal manca, tessera sanitariacodic fiscal, codic fiscal carta) 7 List(condizioni generali servizio, amministrativo modulo modulo, allegato amministrativo modulo, informativa privaci modulo, privaci modulo modulo, allegati prezzi modulo, prezzi modulo modulo, allegato amministrativo agosto, modulo modulo modulo, amministrativo agosto sino) 6 List(emission trasmission fattur, modalita emission trasmission, amministrativo modalita emission, allegato amministrativo modalita, trasmission fattur indirizzo, indirizzo pec obbligatorio, pec obbligatorio fornito, pec allegato amministrativo, fattur indirizzo fisico, indirizzo fisico allegato) 9 List(scheda client sede, client sede legal, sede legal visura, sede legal discordant, legal discordant visura, legal sede legal, sede legal sede, sede legal cap, legal visura cameral, visura cameral sede) 5 List(mancanti fotocopi fronteretro, fotocopi fronteretro tessera, fronteretro carta didentit, fotocopi fronteretro carta, tessera sanitariacodic fiscal, fronteretro tessera sanitariacodic, cf rappresentant legal, mancano fotocopi fronteretro, manca retro codic, retro codic fiscal) 1 List(proposta contrattual specifica, accettazion proposta contrattual, contrattual specifica firma, timbro accettazion proposta, sovrappost timbro accettazion, contrattual specifica firm, esteso sovrappost timbro, leggibili esteso sovrappost, ben leggibili esteso, specifica firma leggibil) 10 List(informativa privaci soggetti, privaci soggetti giuridici, giuridici scelt firma, soggetti giuridici scelt, scelt firma richiedent, firma richiedent firma, leggibil informativa privaci, giuridici scelt scelt, firma richiedent firm, scelt luogo data) 3 List(scheda client sede, client sede legal, legal scheda client, sede legal scheda, legal discordant visura, sede legal cap, visura scheda client, sede legal discordant, cap scheda client, client sede operativa) 8 List(scheda client dati, client dati anagrafici, dati anagrafici social, anagrafici social discordant, social discordant visura, dati anagrafici giuridica, dati anagrafici qualit, anagrafici social visura, visura scheda client, giuridica scheda client) 11 List(accettazion proposta contrattual, proposta contrattual firma, leggibil accettazion proposta, proposta contrattual specifica, firma leggibil accettazion, contrattual firma leggibil, timbro accettazion proposta, proposta contrattual data, proposta contrattual firm, proposta contrattual accettazion) 2 List(forma giuridica errata, completo ragion social, nome nome completo, allegato amministrativo agosto, amministrativo agosto sino, ragion social diversa, sfa crm contratto, ragion social errata, accettazion proposta contrattual, agosto sino trattasi) 4 List(informativa privaci soggetti, privaci soggetti giuridici, professionisti condominio scelt, fisich assimil liberi, liberi professionisti condominio, assimil liberi professionisti, informativa privaci fisich, privaci fisich assimil, soggetti giuridici scelt, giuridici scelt scelt)

In [ ]:
docs_per_topic = predictions_cluster_final.groupby('prediction').agg(concat_ws(' ', collect_list(col("sentence"))).alias('Doc'))

topN_4gram=top_n_words(docs_per_topic, inputCol="Doc", outputCol="features", ngram=4, N=10, targetCol="prediction")

topN_4gram.display()

Uploading artifacts:   0%|          | 0/4 [00:00<?, ?it/s]

prediction topN_words 0 List(documento identit codic fiscal, fotocopi fronteretro carta didentit, carta didentita codic fiscal, codic fiscal legal rappresentant, codic fiscal sottoscrittor contratto, identita codic fiscal client, documento didentit corso validit, identit codic fiscal firmatario, corso validit codic fiscal, didentit corso validit codic) 7 List(allegato amministrativo modulo modulo, informativa privaci modulo modulo, allegati prezzi modulo modulo, allegato amministrativo agosto sino, polici credito modulo modulo, condizioni generali servizio version, privaci modulo modulo informativa, condizioni generali servizio manca, privaci modulo modulo modulo, credito modulo modulo polici) 6 List(modalita emission trasmission fattur, amministrativo modalita emission trasmission, allegato amministrativo modalita emission, emission trasmission fattur indirizzo, indirizzo pec obbligatorio fornito, trasmission fattur indirizzo fisico, indirizzo fisico allegato amministrativo, email pec allegato amministrativo, sfa allegato amministrativo modalita, pec pec errata pec) 9 List(scheda client sede legal, client sede legal discordant, sede legal discordant visura, sede legal sede legal, client sede legal visura, client sede legal sede, client sede legal cap, sede legal visura cameral, visura cameral sede legal, legal discordant visura cameral) 5 List(mancanti fotocopi fronteretro tessera, fotocopi fronteretro carta didentit, fronteretro tessera sanitariacodic fiscal, fotocopi fronteretro tessera sanitariacodic, mancanti fotocopi fronteretro carta, manca retro codic fiscal, fronteretro carta didentit nitid, sfa mancano spunt privaci, tessera sanitariacodic fiscal manca, sanitariacodic fiscal manca retro) 1 List(accettazion proposta contrattual specifica, proposta contrattual specifica firma, timbro accettazion proposta contrattual, sovrappost timbro accettazion proposta, esteso sovrappost timbro accettazion, proposta contrattual specifica firm, ben leggibili esteso sovrappost, leggibili esteso sovrappost timbro, contrattual specifica firma leggibil, accettazion proposta contrattual timbro) 10 List(informativa privaci soggetti giuridici, privaci soggetti giuridici scelt, soggetti giuridici scelt firma, giuridici scelt firma richiedent, scelt firma richiedent firma, leggibil informativa privaci soggetti, soggetti giuridici scelt scelt, scelt firma richiedent firm, soggetti giuridici scelt luogo, giuridici scelt luogo data) 3 List(scheda client sede legal, client sede legal scheda, legal scheda client sede, sede legal scheda client, client sede legal cap, client sede legal discordant, sede legal discordant visura, scheda client sede operativa, visura scheda client sede, scheda client riferimenti client) 8 List(scheda client dati anagrafici, client dati anagrafici social, dati anagrafici social discordant, anagrafici social discordant visura, client dati anagrafici giuridica, client dati anagrafici qualit, social discordant visura cameral, dati anagrafici social visura, visura scheda client dati, anagrafici social visura cameral) 11 List(accettazion proposta contrattual firma, leggibil accettazion proposta contrattual, accettazion proposta contrattual specifica, firma leggibil accettazion proposta, proposta contrattual firma leggibil, timbro accettazion proposta contrattual, accettazion proposta contrattual firm, accettazion proposta contrattual accettazion, accettazion proposta contrattual vigor, contrattual specifica firma leggibil) 2 List(allegato amministrativo agosto sino, sfa crm contratto visura, scheda client sede legal, codic fiscal front retro, riferimenti client system administr, amministrativo agosto sino trattasi, agosto sino trattasi pa, possibil completar verifich anagrafich, proposta contrattual vigor version, condominio scelt spunta scelt) 4 List(informativa privaci soggetti giuridici, privaci soggetti giuridici scelt, liberi professionisti condominio scelt, fisich assimil liberi professionisti, assimil liberi profession

In [ ]:
predictions_cluster_final.groupBy("prediction").count().display()

prediction count 1 782 6 521 3 1509 5 303 9 1031 8 439 7 433 10 1010 11 1180 2 1016 0 472 4 464

In [ ]:
predictions_cluster_final.select("idcase",
    "descrizione","prediction").join(topN,"prediction","left").display()

prediction idcase descrizione topN_words 0 6865606 Occorre allegare il documento di identità, anche in presenza di firma digitale List(didentita codic fiscal, identita codic fiscal, fronteretro carta didentit, documento identit codic, identit codic fiscal, fotocopi fronteretro carta, carta didentita codic, codic fiscal manca, tessera sanitariacodic fiscal, codic fiscal carta) 0 6811188 manca documento d'identità List(didentita codic fiscal, identita codic fiscal, fronteretro carta didentit, documento identit codic, identit codic fiscal, fotocopi fronteretro carta, carta didentita codic, codic fiscal manca, tessera sanitariacodic fiscal, codic fiscal carta) 0 4278278 MANCA CARTA IDENTITA' CODICE FISCALE List(didentita codic fiscal, identita codic fiscal, fronteretro carta didentit, documento identit codic, identit codic fiscal, fotocopi fronteretro carta, carta didentita codic, codic fiscal manca, tessera sanitariacodic fiscal, codic fiscal carta) 7 4711092 si chiede la cortesia di inviare il contratto sotto forma di unico file .PDF , comprensivo di contratto e di tutti i documenti, possibilmente non di dimensioni troppo piccole. List(condizioni generali servizio, amministrativo modulo modulo, allegato amministrativo modulo, informativa privaci modulo, privaci modulo modulo, allegati prezzi modulo, prezzi modulo modulo, allegato amministrativo agosto, modulo modulo modulo, amministrativo agosto sino) 6 5808821 ALLEGATO AMMINISTRATIVO, MODALITA' DI EMISSIONE E TRASMISSIONE DELLE FATTURE, indirizzo PEC (obbligatorio se non fornito Codice Destinatario), TROPPI ININDIRIZZI O SI METTE EMAIL O SI METTE LA PEC List(emission trasmission fattur, modalita emission trasmission, amministrativo modalita emission, allegato amministrativo modalita, trasmission fattur indirizzo, indirizzo pec obbligatorio, pec obbligatorio fornito, pec allegato amministrativo, fattur indirizzo fisico, indirizzo fisico allegato) 6 3811081 ALLEGATO AMMINISTRATIVO, MODALITA' DI EMISSIONE E TRASMISSIONE DELLE FATTURE, pec List(emission trasmission fattur, modalita emission trasmission, amministrativo modalita emission, allegato amministrativo modalita, trasmission fattur indirizzo, indirizzo pec obbligatorio, pec obbligatorio fornito, pec allegato amministrativo, fattur indirizzo fisico, indirizzo fisico allegato) 6 4699543 ALLEGATO AMMINISTRATIVO, MODALITA' DI EMISSIONE E TRASMISSIONE DELLE FATTURE, indirizzo fisico List(emission trasmission fattur, modalita emission trasmission, amministrativo modalita emission, allegato amministrativo modalita, trasmission fattur indirizzo, indirizzo pec obbligatorio, pec obbligatorio fornito, pec allegato amministrativo, fattur indirizzo fisico, indirizzo fisico allegato) 6 5165540 ALLEGATO AMMINISTRATIVO, MODALITA' DI EMISSIONE E TRASMISSIONE DELLE FATTURE, Codice Destinatario: mancante List(emission trasmission fattur, modalita emission trasmission, amministrativo modalita emission, allegato amministrativo modalita, trasmission fattur indirizzo, indirizzo pec obbligatorio, pec obbligatorio fornito, pec allegato amministrativo, fattur indirizzo fisico, indirizzo fisico allegato) 9 3884658 SCHEDA CLIENTE, SEDE LEGALE, Via, inserire dati sede legale sul contratto List(scheda client sede, client sede legal, sede legal visura, sede legal discordant, legal discordant visura, legal sede legal, sede legal sede, sede legal cap, legal visura cameral, visura cameral sede) 9 633673 SCHEDA CLIENTE, SEDE LEGALE, Località, localita discordante con la cerved : padova List(scheda client sede, client sede legal, sede legal visura, sede legal discordant, legal discordant visura, legal sede legal, sede legal sede, sede legal cap, legal visura cameral, visura cameral sede) 9 6029098 SCHEDA CLIENTE, SEDE LEGALE, Via, da cerved la sede legale risulta in via giolitti 22 - allineare List(scheda client sede, client sede legal, sede legal visura, sede legal discordant, legal discordant visura, legal sede legal, sede legal sede, sede legal cap, legal v